In [5]:
import pandas as pd
import torch
from transformers import AutoTokenizer, AutoModelForCausalLM, TrainingArguments, Trainer, BitsAndBytesConfig, EarlyStoppingCallback, PreTrainedTokenizer
from torch.utils.data import DataLoader
import sys
from peft import LoraConfig, get_peft_model, TaskType
from huggingface_hub import snapshot_download
import os
import re
import contextlib #helps make pip silent
import sys
import os
import numpy as np

with contextlib.redirect_stdout(sys.__stdout__), contextlib.redirect_stderr(sys.__stderr__):
    %pip install datasets
    %pip install sql_metadata
""""
with contextlib.redirect_stdout(sys.__stdout__), contextlib.redirect_stderr(sys.__stderr__):
    %pip install datasets
    %pip install sql_metadata
"""
from datasets import Dataset
from sql_metadata import Parser
from transformers import AutoTokenizer, AutoModelForCausalLM
from rag_metadata import SQLMetadataRetriever

In [6]:
is_google_colab = False
use_bnb = False

In [7]:
current_read_path = "./"
current_write_path = "./"

def read_path(rel_path):
    return os.path.join(current_read_path, rel_path)

def write_path(rel_path):
    return os.path.join(current_write_path, rel_path)

if is_google_colab:
    from google.colab import drive
    drive.mount('/content/drive')
    current_write_path = "/content/drive/MyDrive/sql_gen"

    hugging_face_path = snapshot_download(
        repo_id="USC-Applied-NLP-Group/SQL-Generation",
        repo_type="model",
        allow_patterns=["train-data/*", "deepseek-coder-1.3b-instruct/*", "src/*", "nba-data/*"],
    )
    sys.path.append(hugging_face_path)
    current_read_path = hugging_face_path
else:
    base_path = os.getcwd()  # Use current working directory in notebooks
    sys.path.append(os.path.abspath(os.path.join(base_path, '../..')))

In [8]:
MODEL_DIR = write_path("rag-rank-16")

## Prepare Model

In [10]:
# Load dataset
df_train = pd.read_csv(read_path("train-data/train_set.tsv"), sep='\t')
df_test = pd.read_csv(read_path("train-data/test_set.tsv"), sep='\t')

# Fix any spacing issues
df_train.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)
df_test.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)

# Display dataset info
print(f"Total train dataset examples: {len(df_train)}")
print(df_train.head())
print(f"Total test dataset examples: {len(df_test)}")
print(df_test.head())
# Load tokenizer
model_name = read_path("deepseek-coder-1.3b-instruct")
tokenizer = AutoTokenizer.from_pretrained(model_name)

# Enable 8-bit quantization for lower memory usage
bnb_config = None
if use_bnb:
    bnb_config = BitsAndBytesConfig(
        load_in_8bit=True,
        bnb_8bit_compute_dtype=torch.float16
    )

# Load model with quantization
#device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device_name = 'cuda:0' if torch.cuda.is_available() else 'cpu'
device = torch.device(device_name)
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    quantization_config=bnb_config,
    device_map=device
)

special_token = "<|endofsql|>"

# Only add if it doesn’t already exist
#if special_token not in tokenizer.get_vocab():
#print("adding!")
#print(len(tokenizer))
tokenizer.add_special_tokens({"additional_special_tokens": [special_token]})
tokenizer.eos_token = special_token
model.resize_token_embeddings(len(tokenizer))

tokenizer.truncation_side = "left"


C:\Users\Dean\AppData\Local\Temp\ipykernel_22484\3262638624.py:6: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_train.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)
C:\Users\Dean\AppData\Local\Temp\ipykernel_22484\3262638624.py:7: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_test.applymap(lambda x: re.sub(r'\s+', ' ', x) if isinstance(x, str) else x)


Total train dataset examples: 2143
                                       natural_query  \
0  Which NBA teams were established after the yea...   
1  What is the most points the Los Angeles Lakers...   
2  What is the second-highest number of points th...   
3  How many home games did the Golden State Warri...   
4  What is the average number of assists by the B...   

                                           sql_query                result  
0  SELECT full_name FROM team WHERE year_founded ...  New Orleans Pelicans  
1  SELECT MAX(pts_home) FROM game  WHERE team_nam...                   162  
2  SELECT pts_home FROM game WHERE team_name_home...                   156  
3  SELECT COUNT(*)  FROM game  WHERE team_abbrevi...                    29  
4  SELECT AVG(ast_home)  FROM game  WHERE team_ab...           26.51355662  
Total test dataset examples: 150
                                       natural_query  \
0  What is the average number of fg_pct in home g...   
1  How many lead chan

## Prepare RAG

In [11]:
retriever = SQLMetadataRetriever()

metadata_docs = [
    '''team Table
Stores information about NBA teams.
CREATE TABLE IF NOT EXISTS "team" (
  "id" TEXT PRIMARY KEY,      -- Unique identifier for the team
  "full_name" TEXT,           -- Full official name of the team (e.g., "Los Angeles Lakers")
  "abbreviation" TEXT,        -- Shortened team name (e.g., "LAL")
  "nickname" TEXT,            -- Commonly used nickname for the team (e.g., "Lakers")
  "city" TEXT,                -- City where the team is based
  "state" TEXT,               -- State where the team is located
  "year_founded" REAL         -- Year the team was established
);
''',
    '''game Table
Contains detailed statistics for each NBA game, including home and away team performance.
CREATE TABLE IF NOT EXISTS "game" (
  "season_id" TEXT,            -- Season identifier, formatted as "2YYYY" (e.g., "21970" for the 1970 season)
  "team_id_home" TEXT,         -- ID of the home team (matches "id" in team table)
  "team_abbreviation_home" TEXT, -- Abbreviation of the home team
  "team_name_home" TEXT,       -- Full name of the home team
  "game_id" TEXT PRIMARY KEY,  -- Unique identifier for the game
  "game_date" TIMESTAMP,       -- Date the game was played (YYYY-MM-DD format)
  "matchup_home" TEXT,         -- Matchup details including opponent (e.g., "LAL vs. BOS")
  "wl_home" TEXT,              -- "W" if the home team won, "L" if they lost
  "min" INTEGER,               -- Total minutes played in the game
  "fgm_home" REAL,             -- Field goals made by the home team
  "fga_home" REAL,             -- Field goals attempted by the home team
  "fg_pct_home" REAL,          -- Field goal percentage of the home team
  "fg3m_home" REAL,            -- Three-point field goals made by the home team
  "fg3a_home" REAL,            -- Three-point attempts by the home team
  "fg3_pct_home" REAL,         -- Three-point field goal percentage of the home team
  "ftm_home" REAL,             -- Free throws made by the home team
  "fta_home" REAL,             -- Free throws attempted by the home team
  "ft_pct_home" REAL,          -- Free throw percentage of the home team
  "oreb_home" REAL,            -- Offensive rebounds by the home team
  "dreb_home" REAL,            -- Defensive rebounds by the home team
  "reb_home" REAL,             -- Total rebounds by the home team
  "ast_home" REAL,             -- Assists by the home team
  "stl_home" REAL,             -- Steals by the home team
  "blk_home" REAL,             -- Blocks by the home team
  "tov_home" REAL,             -- Turnovers by the home team
  "pf_home" REAL,              -- Personal fouls by the home team
  "pts_home" REAL,             -- Total points scored by the home team
  "plus_minus_home" INTEGER,   -- Plus/minus rating for the home team
  "video_available_home" INTEGER, -- Indicates whether video is available (1 = Yes, 0 = No)
  "team_id_away" TEXT,         -- ID of the away team
  "team_abbreviation_away" TEXT, -- Abbreviation of the away team
  "team_name_away" TEXT,       -- Full name of the away team
  "matchup_away" TEXT,         -- Matchup details from the away team’s perspective
  "wl_away" TEXT,              -- "W" if the away team won, "L" if they lost
  "fgm_away" REAL,             -- Field goals made by the away team
  "fga_away" REAL,             -- Field goals attempted by the away team
  "fg_pct_away" REAL,          -- Field goal percentage of the away team
  "fg3m_away" REAL,            -- Three-point field goals made by the away team
  "fg3a_away" REAL,            -- Three-point attempts by the away team
  "fg3_pct_away" REAL,         -- Three-point field goal percentage of the away team
  "ftm_away" REAL,             -- Free throws made by the away team
  "fta_away" REAL,             -- Free throws attempted by the away team
  "ft_pct_away" REAL,          -- Free throw percentage of the away team
  "oreb_away" REAL,            -- Offensive rebounds by the away team
  "dreb_away" REAL,            -- Defensive rebounds by the away team
  "reb_away" REAL,             -- Total rebounds by the away team
  "ast_away" REAL,             -- Assists by the away team
  "stl_away" REAL,             -- Steals by the away team
  "blk_away" REAL,             -- Blocks by the away team
  "tov_away" REAL,             -- Turnovers by the away team
  "pf_away" REAL,              -- Personal fouls by the away team
  "pts_away" REAL,             -- Total points scored by the away team
  "plus_minus_away" INTEGER,   -- Plus/minus rating for the away team
  "video_available_away" INTEGER, -- Indicates whether video is available (1 = Yes, 0 = No)
  "season_type" TEXT           -- Regular season or playoffs
);
''',
    '''other_stats Table
Stores additional statistics, linked to the game table via game_id.
CREATE TABLE IF NOT EXISTS "other_stats" (
  "game_id" TEXT,             -- Unique game identifier, matches id column from game table
  "league_id" TEXT,           -- League identifier
  "team_id_home" TEXT,        -- Home team identifier
  "team_abbreviation_home" TEXT, -- Home team abbreviation
  "team_city_home" TEXT,      -- Home team city
  "pts_paint_home" INTEGER,   -- Points in the paint by the home team
  "pts_2nd_chance_home" INTEGER, -- Second chance points by the home team
  "pts_fb_home" INTEGER,      -- Fast break points by the home team
  "largest_lead_home" INTEGER,-- Largest lead by the home team
  "lead_changes" INTEGER,     -- Number of lead changes 
  "times_tied" INTEGER,       -- Number of times the score was tied
  "team_turnovers_home" INTEGER, -- Home team turnovers
  "total_turnovers_home" INTEGER, -- Total turnovers by the home team
  "team_rebounds_home" INTEGER, -- Home team rebounds
  "pts_off_to_home" INTEGER,  -- Points off turnovers by the home team
  "team_id_away" TEXT,        -- Away team identifier
  "team_abbreviation_away" TEXT,  -- Away team abbreviation
  "pts_paint_away" INTEGER,   -- Points in the paint by the away team
  "pts_2nd_chance_away" INTEGER, -- Second chance points by the away team
  "pts_fb_away" INTEGER,      -- Fast break points by the away team
  "largest_lead_away" INTEGER,-- Largest lead by the away team
  "team_turnovers_away" INTEGER, -- Away team turnovers
  "total_turnovers_away" INTEGER, -- Total turnovers by the away team
  "team_rebounds_away" INTEGER, -- Away team rebounds
  "pts_off_to_away" INTEGER   -- Points off turnovers by the away team
);
'''
]

retriever.add_documents(metadata_docs)

c:\Users\Dean\AppData\Local\Programs\Python\Python312\Lib\site-packages\transformers\models\bert\modeling_bert.py:440: UserWarning: 1Torch was not compiled with flash attention. (Triggered internally at C:\actions-runner\_work\pytorch\pytorch\builder\windows\pytorch\aten\src\ATen\native\transformers\cuda\sdp_utils.cpp:555.)
  attn_output = torch.nn.functional.scaled_dot_product_attention(


## Tokenize and Mask Training Examples

In [12]:


def format_deepseek_chat(example, tokenizer, special_token="<|endofsql|>"):
    # Manually build the prompt as one flat string
    relevant_schemas = retriever.retrieve(example["natural_query"], top_k=1)
    schema_block = "\n\n".join(relevant_schemas)

    input_prompt = f"""
You are an AI assistant that generates SQLite queries for an NBA database based on user questions.

### Relevant Schema:
{schema_block}

### Instructions:
- Generate a valid SQLite query to retrieve relevant data from the database.
- Use column names correctly based on the provided schema.
- Output only the SQLite query as plain text.

### Team Name Information:
In the plaintext user questions, only the full team names will be used, but in the queries you may use the full team names or the abbreviations. 
The full team names can be used with the game table, while the abbreviations should be used with the other_stats table.
Notice they are separated by the | character in the following list:

Atlanta Hawks|ATL
Boston Celtics|BOS
Cleveland Cavaliers|CLE
New Orleans Pelicans|NOP
Chicago Bulls|CHI
Dallas Mavericks|DAL
Denver Nuggets|DEN
Golden State Warriors|GSW
Houston Rockets|HOU
Los Angeles Clippers|LAC
Los Angeles Lakers|LAL
Miami Heat|MIA
Milwaukee Bucks|MIL
Minnesota Timberwolves|MIN
Brooklyn Nets|BKN
New York Knicks|NYK
Orlando Magic|ORL
Indiana Pacers|IND
Philadelphia 76ers|PHI
Phoenix Suns|PHX
Portland Trail Blazers|POR
Sacramento Kings|SAC
San Antonio Spurs|SAS
Oklahoma City Thunder|OKC
Toronto Raptors|TOR
Utah Jazz|UTA
Memphis Grizzlies|MEM
Washington Wizards|WAS
Detroit Pistons|DET
Charlotte Hornets|CHA

### Query Guidelines:
Use team_name_home and team_name_away to match teams to the game table. Use team_abbreviation_home and team_abbreviation away to match teams to the other_stats table.

To filter by season, use season_id = '2YYYY'.

Example: To get statistics from 2005, use a statement like: season_id = '22005'. To get statistics from 1972, use a statement like: season_id = "21972". To get statistics from 2015, use a statement like: season_id = "22015".

Ensure queries return relevant columns and avoid unnecessary joins.

### Example User Requests and SQLite Queries
Request:
"What is the most points the Los Angeles Lakers have ever scored at home?"
SQLite:
SELECT MAX(pts_home)
FROM game
WHERE team_name_home = 'Los Angeles Lakers';

Request:
"Which teams are located in the state of California?"
SQLite:
SELECT full_name FROM team WHERE state = 'California';

Request:
"Which team had the highest number of team turnovers in an away game?"
SQLite:
SELECT team_abbreviation_away FROM other_stats ORDER BY team_turnovers_away DESC LIMIT 1;

Request:
"Which teams were founded before 1979?"
SQLite:
SELECT full_name FROM team WHERE year_founded < 1979;

Request:
"Find the Boston Celtics largest home victory margin in the 2008 season."
SQLite:
SELECT MAX(pts_home - pts_away) AS biggest_win
FROM game
WHERE team_name_home = 'Boston Celtics' AND season_id = '22008';

Generate only the SQLite query prefaced by SQLite: and no other text. Now generate an SQLite query for the following user request.
Request:
"""
    prompt = f"{input_prompt}{example['natural_query']}\n"
    completion = f"SQLite:\n{example['sql_query']}{special_token}"

    full_text = prompt + completion
    tokenized = tokenizer(
        full_text,
        truncation=True,
        padding="max_length",
        max_length=3156,  # or whatever your model can handle
    )

    # Mask out prompt tokens in the labels
    prompt_len = len(tokenizer(prompt, truncation=True)["input_ids"])
    labels = tokenized["input_ids"][:]
    labels[:prompt_len] = [-100] * prompt_len
    tokenized["labels"] = labels

    return tokenized

# Build dataset dict
train_dataset_dict = {
    "natural_query": df_train["natural_query"].tolist(),
    "sql_query": df_train["sql_query"].tolist(),
}

val_dataset_dict = {
    "natural_query": df_test["natural_query"].tolist(),
    "sql_query": df_test["sql_query"].tolist(),
}

# Create HuggingFace Dataset
train_dataset = Dataset.from_dict(train_dataset_dict)
val_dataset = Dataset.from_dict(val_dataset_dict)


# Apply formatting
train_dataset = train_dataset.map(
    lambda x: format_deepseek_chat(x, tokenizer),
    remove_columns=["natural_query", "sql_query"]
)

val_dataset = val_dataset.map(
    lambda x: format_deepseek_chat(x, tokenizer),
    remove_columns=["natural_query", "sql_query"]
)

Map: 100%|██████████| 150/150 [00:04<00:00, 37.49 examples/s]


In [13]:
for v in val_dataset:
    print(v)
    print(tokenizer.decode(v['input_ids'], skip_special_tokens=True))
    break



{'input_ids': [32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014, 32014

In [10]:
# Define LoRA configuration
lora_config = LoraConfig(
    r=16,  # Rank of LoRA matrices (adjust for memory vs. accuracy)
    lora_alpha=32,  # Scaling factor
    lora_dropout=0.0,  # Dropout for regularization
    bias="none",
    task_type=TaskType.CAUSAL_LM,
    target_modules=[
        "q_proj",
        "k_proj",
        "v_proj",
        "o_proj",
        "gate_proj",
        "up_proj",
        "down_proj"
    ]
)

# Wrap model with LoRA adapters
model = get_peft_model(model, lora_config)
model = model.to(device)
model.print_trainable_parameters()  # Show trainable parameters count

trainable params: 14,991,360 || all params: 1,361,463,296 || trainable%: 1.1011


In [11]:
training_args = TrainingArguments(
    output_dir=MODEL_DIR,
    eval_strategy="epoch",  # Evaluate at the end of each epoch
    save_strategy="epoch",  # Save model every epoch
    per_device_train_batch_size=1,  # LoRA allows higher batch size
    per_device_eval_batch_size=1,
    gradient_accumulation_steps=16,
    num_train_epochs=10,  # Increase if needed
    learning_rate=5e-5,  # Higher LR since we're only training LoRA layers
    weight_decay=0.001,
    logging_steps=50,  # Print loss every 50 steps
    save_total_limit=2,  # Keep last 4 checkpoints
    bf16=True if torch.cuda.is_available() else False,
    push_to_hub=False,
    load_best_model_at_end=True,
    metric_for_best_model="eval_loss",
    greater_is_better=False
)

# Trainer setup
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    tokenizer=tokenizer,
    callbacks=[EarlyStoppingCallback(early_stopping_patience=2)]
)

<ipython-input-11-319f42a4ed7b>:21: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(
No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


In [ ]:
# Run training
trainer.train()

# Merge LoRA adapters with the base model before saving
model = model.merge_and_unload()
model.save_pretrained(MODEL_DIR)
tokenizer.save_pretrained(MODEL_DIR)

wandb: WARNING The `run_name` is currently set to the same value as `TrainingArguments.output_dir`. If this was not intended, please specify a different run name by setting the `TrainingArguments.run_name` parameter.
wandb: Using wandb-core as the SDK backend.  Please refer to https://wandb.me/wandb-core for more information.
wandb: Currently logged in as: licesma (licesma-usc) to https://api.wandb.ai. Use `wandb login --relogin` to force relogin


In [ ]:

# Prepare query with the same prompt
input_text = "How many points do the Los Angeles Lakers average at home?"
message = [{'role': 'user', 'content': input_prompt + input_text}]
inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

# Generate Tables
outputs = model.generate(
    inputs,
    max_new_tokens=256,
)
model_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)

print("Generated Tables:", model_output)

In [ ]:
import sqlite3 as sql

prompt_length = len(input_prompt)

print(prompt_length)

# Create connection to sqlite3 database
connection = sql.connect(read_path('nba-data/nba.sqlite'))
cursor = connection.cursor()

for v in val_dataset:
    full_example = tokenizer.decode(v["input_ids"], skip_special_tokens=True)
    user_prompt = full_example[:prompt_length]
    question, tables = full_example[prompt_length:].split("Tables:\n")
    print(question)
    print(tables)
    break


In [ ]:
def extract_tables_from_string(s):
    keywords = {"game", "team", "other_stats"}
    found = {k for k in keywords if k in s}
    return found

In [ ]:
def compare_table_lists(actual_tables, generated_tables):
    actual_set = extract_tables_from_string(actual_tables)
    generated_set = extract_tables_from_string(generated_tables)

    # Check if they match
    return generated_set == actual_set

In [ ]:

num_sql_matched = 0

first_actual = []
first_model = []
print("Evaluating...")
for v in val_dataset:
    full_example = tokenizer.decode(v["input_ids"], skip_special_tokens=True)
    user_prompt = full_example[:prompt_length]
    question, training_tables = full_example[prompt_length:].split("Tables:\n")
    #print(question)
    #print(sql_query)

    # Obtain model output
    message = [{'role': 'user', 'content': input_prompt + question}]
    inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

    # Generate SQL query
    outputs = model.generate(
        inputs,
        max_new_tokens=256,
        pad_token_id=tokenizer.eos_token_id,
    )
    model_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
    after_last_colon = model_output.rsplit(":", 1)[-1]
    tables_string = after_last_colon.replace('\n', '').replace('\r', '')
    #print("Training tables:", training_tables)
    #print("Model tables:", tables_string.split(" "))
    first_actual = training_tables
    first_model = tables_string
    result = compare_table_lists(training_tables, tables_string)
    if result:
        num_sql_matched += 1

print("Accuracy :", num_sql_matched/len(val_dataset))



In [ ]:

num_sql_matched = 0

first_actual = []
first_model = []
print("Evaluating...")
for v in val_dataset:
    full_example = tokenizer.decode(v["input_ids"], skip_special_tokens=True)
    user_prompt = full_example[:prompt_length]
    question, training_tables = full_example[prompt_length:].split("Tables:\n")
    #print(question)
    #print(sql_query)

    # Obtain model output
    message = [{'role': 'user', 'content': input_prompt + question}]
    inputs = tokenizer.apply_chat_template(message, add_generation_prompt=True, return_tensors="pt").to(model.device)

    # Generate SQL query
    outputs = model.generate(
        inputs,
        max_new_tokens=256,
        pad_token_id=tokenizer.eos_token_id,
    )
    model_output = tokenizer.decode(outputs[0][len(inputs[0]):], skip_special_tokens=True)
    after_last_colon = model_output.rsplit(":", 1)[-1]
    tables_string = after_last_colon.replace('\n', '').replace('\r', '')
    #print("Training tables:", training_tables)
    #print("Model tables:", tables_string.split(" "))
    first_actual = training_tables
    first_model = tables_string
    result = compare_table_lists(training_tables, tables_string)
    if result:
        num_sql_matched += 1

print("Accuracy :", num_sql_matched/len(val_dataset))



In [ ]:
model = AutoModelForCausalLM.from_pretrained(MODEL_DIR, torch_dtype=torch.bfloat16, device_map=device)
tokenizer = AutoTokenizer.from_pretrained(MODEL_DIR)
